# Download Copernicus ARLIE
Michael Brechbühler, 23.03.2023

This script downloads data from the [Copernicus ARLIE](https://land.copernicus.eu/news/product-update-aggregated-river-and-lake-ice-extent-arlie) based on the provided REST call API and [python functions](https://github.com/eea/clms-hrsi-api-client-python-arlie).

## Import functions

In [22]:
import sys
import os
import holoviews as hv
import pandas as pd
import geopandas as gpd
from datetime import datetime
from hvplot import pandas
import numpy as np
import matplotlib.pyplot as plt

path_cwd = os.getcwd()
path_funcs = path_cwd+"\\functions"
if path_funcs not in sys.path:
    sys.path.append(path_funcs)

from clms_hrsi_arlie_downloader import download_arlie_products

## Load geometries
The ARLIE request needs a geometry in Well-Known Text (WKT) format. One one to obtain one manually is to use [Wicket](http://arthur-e.github.io/Wicket/sandbox-gmaps3.html).

In [23]:
# European Alps
#wkt_polygon = "MULTIPOLYGON (((4.89124342478314 43.2224311821953,4.76366210530728 46.3663994121361,7.33351439760674 47.8426975374997,17.1755019000302 48.6081854543548,16.5922730109977 46.2023662870957,13.9768559617426 45.3913136132849,8.97384564801066 45.3913136132849,8.60932759236534 43.5687233350584,4.89124342478314 43.2224311821953)))"

# FunkyFish Norwegian Lakes
wkt_polygon = "POLYGON((6.578021572940602 59.17358834971748,7.297626065128102 59.17358834971748,7.297626065128102 58.40651425048495,6.578021572940602 58.40651425048495,6.578021572940602 59.17358834971748))"

In [95]:
gs_aoi = gpd.GeoSeries.from_wkt(data=[wkt_polygon], crs='EPSG:4326')
gdf_aoi = gpd.GeoDataFrame({'geometry': gs_aoi})
gdf_aoi

gdf_aoi.hvplot.polygons(geo=True, tiles=True, 
                        color='red', fill_alpha=0.1, line_color='red',
                       xlabel='Longitude', ylabel='Latitude', height=400, label='AOI')

:Overlay
   .Tiles.I      :Tiles   [x,y]
   .Polygons.AOI :Polygons   [Longitude,Latitude]

## Set params

In [52]:
# Get time to set output folder
now = datetime.now()
now_str = now.strftime('%Y%m%d_%H%M%S')

# Set params
outputDir = path_cwd+'\\results\\'+'request_'+now_str+'\\'
startDate = '2015-01-01'
completionDate = '2023-05-22'
geometryWkt = wkt_polygon
cloudCoverageMax = 100
requestGeometries = True
returnMode = 'csv_and_variable'

## Download data

In [49]:
geometries, arlie = download_arlie_products(returnMode, outputDir=outputDir, startDate=startDate, completionDate=completionDate, geometryWkt=geometryWkt, cloudCoverageMax=cloudCoverageMax, requestGeometries=requestGeometries)

Creating directory E:\git\copernicus_arlie\results\request_20230523_085920
Executing request for geometries: https://cryo.land.copernicus.eu/arlie/get_geometries?geometrywkt=POLYGON((6.578021572940602+59.17358834971748%2C7.297626065128102+59.17358834971748%2C7.297626065128102+58.40651425048495%2C6.578021572940602+58.40651425048495%2C6.578021572940602+59.17358834971748))&getonlyids=True
Executing request for geometries: https://cryo.land.copernicus.eu/arlie/get_geometries?geometrywkt=POLYGON((6.578021572940602+59.17358834971748%2C7.297626065128102+59.17358834971748%2C7.297626065128102+58.40651425048495%2C6.578021572940602+58.40651425048495%2C6.578021572940602+59.17358834971748))
Writing geometries in E:\git\copernicus_arlie\results\request_20230523_085920\geometries.csv
Executing request for ARLIE: https://cryo.land.copernicus.eu/arlie/get_arlie?geometrywkt=POLYGON((6.578021572940602+59.17358834971748%2C7.297626065128102+59.17358834971748%2C7.297626065128102+58.40651425048495%2C6.578021

## Load data and inspect geometries

In [109]:
# Load geometries
df_geoms = pd.read_csv(path_cwd+'\\results\\'+'request_'+now_str+'\\geometries.csv', delimiter=';')
df_geoms['area_km2'] = df_geoms['area']/10e5
gdf_geoms_3035 = gpd.GeoDataFrame(df_geoms, geometry=gpd.GeoSeries.from_wkt(data=df_geoms['geometry'], crs='EPSG:3035'))
gdf_geoms_4326 = gdf_geoms_3035.to_crs(crs='EPSG:4326')

# Load lake ice data
df = pd.read_csv(path_cwd+'\\results\\'+'request_'+now_str+'\\arlie.csv', delimiter=';')

# Plot lakes over AOI
gdf_aoi.hvplot.polygons(geo=True, tiles=True, 
                        color='red', fill_alpha=0.1, line_color='red',
                        xlabel='Longitude', ylabel='Latitude', height=500, label='AOI') *\
gdf_geoms_4326.hvplot.polygons(geo=True,
                               color='area_km2', cmap='jet', clabel='Lake area (km^2)', line_color='black',
                               label='Lakes', 
                               hover_cols=['object_nam', 'eu_hydro_id', 'id'])

:Overlay
   .Tiles.I        :Tiles   [x,y]
   .Polygons.AOI   :Polygons   [Longitude,Latitude]
   .Polygons.Lakes :Polygons   [Longitude,Latitude]   (area_km2,object_nam,eu_hydro_id,id)

## Filter out Lake of interest

In [55]:
lakedict = { 
    'Sirdalsvannet': 'IW40002314',
    'Oeyarvatnet': 'IW40002321',
    'Rosskreppfjorden': 'IW40031229'
}

lakename = 'Sirdalsvannet'
eu_hydro_id = lakedict[lakename]

In [56]:
df_id_lut = df_geoms[['eu_hydro_id', 'id']].set_index('eu_hydro_id')
id = df_id_lut.loc[eu_hydro_id].iloc[0]
df_id = df.loc[df['river_km_id'] == id]
df_id['dt64'] = df_id['datetime'].astype(np.datetime64)
df_id

C:\Users\Michael\AppData\Local\Temp\ipykernel_15228\3414803831.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_id['dt64'] = df_id['datetime'].astype(np.datetime64)


id  river_km_id             datetime  water_perc  ice_perc  \
1867296  1867297       348865  2016-09-01T17:19:27          91         6   
1867297  1867298       348865  2016-09-03T05:48:02          94         4   
1867298  1867299       348865  2016-09-08T10:54:16          91         7   
1867299  1867300       348865  2016-09-11T11:04:38           0         0   
1867300  1867301       348865  2016-09-13T17:19:27          91         7   
...          ...          ...                  ...         ...       ...   
1868679  1868680       348865  2023-05-04T17:20:14          91         7   
1868680  1868681       348865  2023-05-05T10:54:54           0         0   
1868681  1868682       348865  2023-05-06T17:04:01          93         4   
1868682  1868683       348865  2023-05-18T17:04:02          94         4   
1868683  1868684       348865  2023-05-20T16:47:24          20         0   

         other_perc  cloud_perc  nd_perc  qc                 source  \
1867296           0           0        3   2  Sentinel-1 Sentinel-2   
1867297           0           0        2   2             Sentinel-1   
1867298           0           0        2   2  Sentinel-1 Sentinel-2   
1867299           0          16       84   0             Sentinel-2   
1867300           0           0        2   2             Sentinel-1   
...             ...         ...      ...  ..                    ...   
1868679           0           0        2   2  Sentinel-1 Sentinel-2   
1868680           0          98        2   0             Sentinel-2   
1868681           0           0        3   2  Sentinel-1 Sentinel-2   
1868682           0           0        2   2  Sentinel-1 Sentinel-2   
1868683           1          78        1   0  Sentinel-1 Sentinel-2   

                       dt64  
1867296 2016-09-01 17:19:27  
1867297 2016-09-03 05:48:02  
1867298 2016-09-08 10:54:16  
1867299 2016-09-11 11:04:38  
1867300 2016-09-13 17:19:27  
...                     ...  
1868679 2023-05-04 17:20:14  
1868680 2023-05-05 10:54:54  
1868681 2023-05-06 17:04:01  
1868682 2023-05-18 17:04:02  
1868683 2023-05-20 16:47:24  

[1388 rows x 11 columns]

## Inspect data

In [124]:
# Define quality flags to be allowed
qc_allowed = [0,1,2,3]

# Quality flag dictionary
qc_dict = {
    0:'high quality',
    1:'medium quality',
    2:'low quality',
    3:'minimal quality'
}

In [125]:
lic_arlie = df_id.set_index('dt64')
lic_arlie = lic_arlie[lic_arlie['qc'].isin(qc_allowed)].replace({'qc':qc_dict})
plot = lic_arlie.hvplot(y='ice_perc', by='qc', kind='scatter', width=1500, height=300,
           clabel='quality', title=f'Copernicus ARLIE: Lake {lakename} ({eu_hydro_id})',
                xlabel='Date', ylabel='Ice coverage (%)') * \
        lic_arlie.hvplot.area(y='ice_perc', alpha=0.4)
plot

:Overlay
   .NdOverlay.I :NdOverlay   [qc]
      :Scatter   [dt64]   (ice_perc)
   .Area.I      :Area   [dt64]   (ice_perc)

## Export data

In [126]:
# Create output folder
path_export = path_cwd+f'\\output\\{eu_hydro_id}_{lakename}_RIVERKM{id}_arlie'
if not os.path.exists(path_export):
    os.makedirs(path_export)

# Save LIC data and plot
lic_arlie.to_csv(path_export+'\\lic_arlie.csv')
hv.save(plot, path_export+'\\lic_arlie.html', fmt='html')
print(f'Data for Lake {lakename} saved to {path_export}.')

Data for Lake Sirdalsvannet saved to E:\git\copernicus_arlie\output\IW40002314_Sirdalsvannet_RIVERKM348865_arlie.
